In [1]:
pip install tiingo[pandas]

In [2]:
from tiingo import TiingoClient

config = {}
config['session'] = True
config['api_key'] = "2231616493a1b03513e42afd2add8ff6f7811b05"

# Initialize
client = TiingoClient(config)

df = client.get_dataframe('TSLA', frequency='1hour', startDate='2017-03-06',endDate='2020-12-27')
df.reset_index(inplace=True)

In [3]:
data = df

In [ ]:
data.date = data.date.dt.strftime('%Y-%m-%d %H:%M:%S')
data = data.set_index('date')
print(data)

In [5]:
import itertools
import multiprocessing
import numpy as np

short_parameters = range(5,7)
long_parameters = range(20,30,5)

paramlist = list(itertools.product(short_parameters,long_parameters))
print(paramlist)

def MovingAverage(params):

  data['smav'] = data.close.rolling(window=params[0]).mean()
  data['lmav'] = data.close.rolling(window = params[1]).mean()
  data['apo'] = data.smav - data.lmav
  data['params'] = 'S =' + ' ' + str(params[0]) + ' ' + 'L =' + ' ' + str(params[1])

  return data

pool = multiprocessing.Pool()
results  = pool.map(MovingAverage,paramlist)

[(5, 20), (5, 25), (6, 20), (6, 25)]


In [ ]:
data = results[1].dropna()
print(data)

In [7]:
import pandas as pd
pd.set_option("display.max_rows", 10001)

eventlong = []
eventshort = []
quantity = []
execution = []

quantity.append(0)
qty = 0
execution = []

eventlong = False
eventshort = False
executionprice = None

for i in range(1,len(data)):

  if data.apo[i-1] < 0 and data.apo[i] > 0:
    eventlong = True
    executionprice = pd.DataFrame({'Trade': 'OpenLong', 'ExPrice': data.open[i+1]}, index = [data.index[i+1]])
    qty += 3
    execution.append(executionprice)
  
  if data.apo[i-1] > 0 and data.apo[i] < 0:
    eventshort = True
    executionprice = pd.DataFrame({'Trade': 'OpenShort', 'ExPrice': data.open[i+1]}, index = [data.index[i+1]])
    qty -= 10
    execution.append(executionprice)
  
  if eventlong == True and data.apo[i-1] > 0 and data.apo[i] < 0:
    executionprice = pd.DataFrame({'Trade': 'CloseLong', 'ExPrice': data.close[i]}, index = [data.index[i]])
    qty -= 3
    eventlong = False
    execution.append(executionprice)

  if eventshort == True and data.apo[i-1] < 0 and data.apo[i] > 0:
    executionprice = pd.DataFrame({'Trade': 'CloseShort', 'ExPrice': data.close[i]}, index = [data.index[i]])
    qty += 10
    eventshort = False
    execution.append(executionprice)
  
  quantity.append(qty)

strategy = pd.DataFrame({'open': data.open, 'close': data.close, 'apo': data.apo, 'Qty': quantity})
strategy = pd.merge(strategy, pd.concat(execution), how='left', left_index=True, right_index=True)
strategy['Qty'] = strategy['Qty'] = strategy['Qty'].shift()

In [14]:
strategy

open     close         apo   Qty       Trade   ExPrice
2017-03-10 18:00:00   243.310   243.320    -2.95420   NaN         NaN       NaN
2017-03-10 19:00:00   243.640   243.630    -2.88000   0.0         NaN       NaN
2017-03-10 20:00:00   243.590   243.645    -2.88680   0.0         NaN       NaN
2017-03-10 21:00:00   243.645   243.645    -2.79640   0.0         NaN       NaN
2017-03-13 14:00:00   243.520   245.620    -2.17240   0.0         NaN       NaN
2017-03-13 15:00:00   245.650   246.330    -1.44960   0.0         NaN       NaN
2017-03-13 16:00:00   246.200   246.000    -0.87200   0.0         NaN       NaN
2017-03-13 17:00:00   246.000   245.440    -0.38700   0.0         NaN       NaN
2017-03-13 18:00:00   245.260   245.160     0.08200   0.0         NaN       NaN
2017-03-13 19:00:00   245.070   246.130     0.25040   3.0    OpenLong   245.070
2017-03-13 20:00:00   246.130   246.130     0.33480   3.0         NaN   245.070
2017-03-14 14:00:00   247.130   247.610     0.71920   3.0         NaN   245.070
2017-03-14 15:00:00   247.490   251.610     1.80160   3.0         NaN   245.070
2017-03-14 16:00:00   251.670   253.690     3.23280   3.0         NaN   245.070
2017-03-14 17:00:00   253.915   256.770     4.96280   3.0         NaN   245.070
2017-03-14 18:00:00   256.520   256.790     6.72200   3.0         NaN   245.070
2017-03-14 19:00:00   256.825   258.050     8.36280   3.0         NaN   245.070
2017-03-14 20:00:00   258.050   258.050     9.13160   3.0         NaN   245.070
2017-03-15 14:00:00   258.050   258.050     9.46240   3.0         NaN   245.070
2017-03-15 15:00:00   258.050   258.050     9.14320   3.0         NaN   245.070
2017-03-15 16:00:00   258.050   258.050     8.86780   3.0         NaN   245.070
2017-03-15 17:00:00   258.050   258.050     8.34040   3.0         NaN   245.070
2017-03-15 18:00:00   258.050   258.050     7.82120   3.0         NaN   245.070
2017-03-15 19:00:00   258.050   258.050     7.28080   3.0         NaN   245.070
2017-03-15 20:00:00   258.050   258.050     6.69120   3.0         NaN   245.070
2017-03-16 14:00:00   261.030   261.000     6.57400   3.0         NaN   245.070
2017-03-16 15:00:00   261.000   264.490     7.02760   3.0         NaN   245.070
2017-03-16 16:00:00   264.490   264.625     7.50340   3.0         NaN   245.070
2017-03-16 17:00:00   264.625   263.960     7.87280   3.0         NaN   245.070
2017-03-16 18:00:00   264.130   263.260     8.20920   3.0         NaN   245.070
2017-03-16 19:00:00   263.250   262.115     7.80080   3.0         NaN   245.070
2017-03-16 20:00:00   262.115   262.115     6.68120   3.0         NaN   245.070
2017-03-17 14:00:00   263.430   263.150     5.67780   3.0         NaN   245.070
2017-03-17 15:00:00   263.190   264.100     4.94820   3.0         NaN   245.070
2017-03-17 16:00:00   264.105   264.810     4.51100   3.0         NaN   245.070
2017-03-17 17:00:00   264.810   263.395     4.07640   3.0         NaN   245.070
2017-03-17 18:00:00   263.450   262.570     3.56900   3.0         NaN   245.070
2017-03-17 19:00:00   262.480   261.245     2.80260   3.0         NaN   245.070
2017-03-17 20:00:00   261.245   261.245     1.92940   3.0         NaN   245.070
2017-03-20 14:00:00   260.000   263.330     1.37100   3.0         NaN   245.070
2017-03-20 15:00:00   263.380   262.950     1.03560   3.0         NaN   245.070
2017-03-20 16:00:00   262.950   262.480     0.84040   3.0         NaN   245.070
2017-03-20 17:00:00   262.480   261.390     0.73580   3.0         NaN   245.070
2017-03-20 18:00:00   261.540   261.025     0.57280   3.0         NaN   245.070
2017-03-20 19:00:00   261.025   261.910     0.13440   3.0         NaN   245.070
2017-03-20 20:00:00   261.910   261.910    -0.22800   3.0   CloseLong   261.910
2017-03-21 14:00:00   264.575   259.920    -0.81480 -10.0   OpenShort   264.575
2017-03-21 15:00:00   260.180   256.020    -1.80760 -10.0         NaN   264.575
2017-03-21 16:00:00   255.510   253.800    -3.08260 -10.0         NaN   264.575
2017-03-21 17:00:00   253

In [9]:
strategy.ExPrice = strategy.ExPrice.fillna(method='ffill')


In [74]:
# initial_capital = 1000
fee_to_open = 1.5
fee_to_close = 1.5
# tax = 0
# margin = 0.2
# leverage = 1/margin

# buysellprice = []
# sellprice = [] 
# tradesize = [] 
# margin = [] 

# tpnl = [] 
# ppnl = [] 
# fees = []
# cash = []
# balance = []
# position = []

# buysellprice.append(0), tradesize.append(0), sellprice.append(0), margin.append(0), upnl.append(0), rpnl.append(0), 
# tpnl.append(0), ppnl.append(0), fees.append(0), cash.append(initial_capital), balance.append(initial_capital)
margin = [] 
margin.append(0)
upnl = [] 
upnl.append(0)
rpnl = []
rpnl.append(0)
exprice = []
exprice.append(0)
pos = []
pos.append(0)

starttrade = []
starttrade.append(0)

ex_price = None
Margin = None
position = False

StartTrade = False

for i in range(1,len(strategy)):

  if strategy.Trade[i] == 'OpenLong':
     StartTrade = True
     position = 'OpenLong'
     ex_price = strategy.ExPrice[i]
     Margin = ex_price * abs(strategy.Qty[i]) * 0.2
  
  if strategy.Trade[i] == 'OpenShort':
    StartTrade = True
    position = 'OpenShort'
    ex_price = strategy.ExPrice[i]

  if StartTrade == True:
    UPnL = (strategy.close[i] - strategy.ExPrice[i]) * abs(strategy.Qty[i]) 
    RPnL = 0
    if strategy.Trade[i] == 'CloseLong' and StartTrade == True:
      RPnL = (strategy.close[i] - ex_price) * abs(strategy.Qty[i]) - (fee_to_open + fee_to_close)
      StartTrade = False
    if strategy.Trade[i] == 'CloseShort' and StartTrade == True:
      RPnL = (ex_price - strategy.close[i]) * abs(strategy.Qty[i]) - (fee_to_open + fee_to_close)
      StartTrade = False

  upnl.append(UPnL), rpnl.append(RPnL), margin.append(Margin)
    
strategy = strategy.assign(UPnL=pd.Series(upnl, index=strategy.index))
strategy = strategy.assign(RPnL=pd.Series(rpnl, index=strategy.index))
strategy = strategy.assign(Margin=pd.Series(margin, index=strategy.index))

In [75]:
round(strategy,3)

open     close  ...  StartTrade      RPnL
2017-03-10 18:00:00   243.310   243.320  ...           0     0.000
2017-03-10 19:00:00   243.640   243.630  ...       False     0.000
2017-03-10 20:00:00   243.590   243.645  ...       False     0.000
2017-03-10 21:00:00   243.645   243.645  ...       False     0.000
2017-03-13 14:00:00   243.520   245.620  ...       False     0.000
2017-03-13 15:00:00   245.650   246.330  ...       False     0.000
2017-03-13 16:00:00   246.200   246.000  ...       False     0.000
2017-03-13 17:00:00   246.000   245.440  ...       False     0.000
2017-03-13 18:00:00   245.260   245.160  ...       False     0.000
2017-03-13 19:00:00   245.070   246.130  ...        True     0.000
2017-03-13 20:00:00   246.130   246.130  ...        True     0.000
2017-03-14 14:00:00   247.130   247.610  ...        True     0.000
2017-03-14 15:00:00   247.490   251.610  ...        True     0.000
2017-03-14 16:00:00   251.670   253.690  ...        True     0.000
2017-03-14 17:00:00   253.915   256.770  ...        True     0.000
2017-03-14 18:00:00   256.520   256.790  ...        True     0.000
2017-03-14 19:00:00   256.825   258.050  ...        True     0.000
2017-03-14 20:00:00   258.050   258.050  ...        True     0.000
2017-03-15 14:00:00   258.050   258.050  ...        True     0.000
2017-03-15 15:00:00   258.050   258.050  ...        True     0.000
2017-03-15 16:00:00   258.050   258.050  ...        True     0.000
2017-03-15 17:00:00   258.050   258.050  ...        True     0.000
2017-03-15 18:00:00   258.050   258.050  ...        True     0.000
2017-03-15 19:00:00   258.050   258.050  ...        True     0.000
2017-03-15 20:00:00   258.050   258.050  ...        True     0.000
2017-03-16 14:00:00   261.030   261.000  ...        True     0.000
2017-03-16 15:00:00   261.000   264.490  ...        True     0.000
2017-03-16 16:00:00   264.490   264.625  ...        True     0.000
2017-03-16 17:00:00   264.625   263.960  ...        True     0.000
2017-03-16 18:00:00   264.130   263.260  ...        True     0.000
2017-03-16 19:00:00   263.250   262.115  ...        True     0.000
2017-03-16 20:00:00   262.115   262.115  ...        True     0.000
2017-03-17 14:00:00   263.430   263.150  ...        True     0.000
2017-03-17 15:00:00   263.190   264.100  ...        True     0.000
2017-03-17 16:00:00   264.105   264.810  ...        True     0.000
2017-03-17 17:00:00   264.810   263.395  ...        True     0.000
2017-03-17 18:00:00   263.450   262.570  ...        True     0.000
2017-03-17 19:00:00   262.480   261.245  ...        True     0.000
2017-03-17 20:00:00   261.245   261.245  ...        True     0.000
2017-03-20 14:00:00   260.000   263.330  ...        True     0.000
2017-03-20 15:00:00   263.380   262.950  ...        True     0.000
2017-03-20 16:00:00   262.950   262.480  ...        True     0.000
2017-03-20 17:00:00   262.480   261.390  ...        True     0.000
2017-03-20 18:00:00   261.540   261.025  ...        True     0.000
2017-03-20 19:00:00   261.025   261.910  ...        True     0.000
2017-03-20 20:00:00   261.910   261.910  ...       False    47.520
2017-03-21 14:00:00   264.575   259.920  ...        True     0.000
2017-03-21 15:00:00   260.180   256.020  ...        True     0.000
2017-03-21 16:00:00   255.510   253.800  ...        True     0.000
2017-03-21 17:00:00   253.820   251.770  ...        True     0.000
2017-03-21 18:00:00   252.000   253.510  ...        True     0.000
2017-03-21 19:00:00   253.600   250.780  ...        True     0.000
2017-03-21 20:00:00   250.780   250.780  ...        True     0.000
2017-03-22 14:00:00   250.780   250.780  ...        True     0.000
2017-03-22 15:00:00   250.780   250.780  ...        True     0.000
2017-03-22 16:00:00   250.780   250.780  ...        True     0.000
2017-03-22 17:00:00   250.780   250.780  ...        True     0.000
2017-03-22 18:00:00   250.780   250.780  ...        True     0.000
2017-03-22 19:00:00   250.780   250.780  ...        True     0.000
2017-